In [1]:
from keras.datasets import mnist
from keras.layers import Input, Dense, Reshape, Flatten, Dropout
from keras.layers import BatchNormalization, Activation, ZeroPadding2D
from keras.layers.advanced_activations import LeakyReLU
from keras.models import Sequential, Model
from keras.optimizers import Adam

import plotly
import plotly.plotly as py
from plotly.offline import iplot
import plotly.graph_objs as go

import matplotlib.pyplot as plt

import h5py

import sys

import numpy as np

Using TensorFlow backend.


In [2]:
plotly.offline.init_notebook_mode()

In [3]:
def load_data():
    data_filename = "../generation/TXTtoHDF5/eminus_Ele-Eta0-Phi0-Energy50.h5"
    data_file = h5py.File(data_filename, 'r')
    np_data = np.array(data_file['layer_0'])

    np.random.shuffle(np_data)
    training_size = int(np_data.shape[0]*0.8)
    training, testing = np_data[:training_size,:,:], np_data[training_size:,:,:]

    return training, testing


In [4]:
def plot_heatmap(data, name):
    data_points = go.Heatmap(z=data)
    plot_data=[data_points]
    iplot(plot_data, filename="jupyter/{}".format(name))

In [5]:
def save_imgs(epoch):
    noise = np.random.normal(0, 1,(1, 100))
    gen_imgs = generator.predict(noise)
    plot_heatmap(np.squeeze(gen_imgs[0],axis=2),"Plot")
    # Rescale images 0 - 1
    #gen_imgs = 0.5 * gen_imgs + 0.5

    #fig, axs = plt.subplots(r, c)
    #cnt = 0
    #for i in range(r):
    #    for j in range(c):
    #        axs[i,j].imshow(gen_imgs[cnt, :,:,0], cmap='gray')
    #        axs[i,j].axis('off')
    #        cnt += 1
    #fig.savefig("generated_images/electron_cal%d.png" % epoch)
    #plt.close()

In [6]:
def build_generator():
    noise_shape = (100,)
        
    model = Sequential()

    model.add(Dense(32, input_shape=noise_shape))
    model.add(LeakyReLU(alpha=0.2))
    model.add(BatchNormalization(momentum=0.8))
    
    #model.add(Dense(128))
    #model.add(LeakyReLU(alpha=0.2))
    #model.add(BatchNormalization(momentum=0.8))
    #model.add(Dense(1024))
    #model.add(LeakyReLU(alpha=0.2))
    #model.add(BatchNormalization(momentum=0.8))
    model.add(Dense(np.prod(img_shape), activation='tanh'))
    model.add(Reshape(img_shape))

    model.summary()

    noise = Input(shape=noise_shape)
    img = model(noise)

    return Model(noise, img)

In [7]:
def build_discriminator():

    img_shape = (img_rows, img_cols, channels)
        
    model = Sequential()

    model.add(Flatten(input_shape=img_shape))
    model.add(Dense(512))
    model.add(LeakyReLU(alpha=0.2))
    model.add(Dense(256))
    model.add(LeakyReLU(alpha=0.2))
    model.add(Dense(1, activation='sigmoid'))
    model.summary()

    img = Input(shape=img_shape)
    validity = model(img)

    return Model(img, validity)

In [8]:
def train(epochs, batch_size=128, save_interval=50):

    # Load the dataset
    #(X_train, _), (_, _) = mnist.load_data()
    X_train, _ = load_data()

    # Logscale?
    #X_train = np.log10(X_train)
    X_train = np.expand_dims(X_train, axis=3)

    half_batch = int(batch_size / 2)

    for epoch in range(epochs):

        # ---------------------
        #  Train Discriminator
        # ---------------------

        # Select a random half batch of images
        idx = np.random.randint(0, X_train.shape[0], half_batch)
        imgs = X_train[idx]

        noise = np.random.normal(0, 1, (half_batch, 100))

        # Generate a half batch of new images
        gen_imgs = generator.predict(noise)

        # Train the discriminator
        d_loss_real = discriminator.train_on_batch(imgs, np.ones((half_batch, 1)))
        d_loss_fake = discriminator.train_on_batch(gen_imgs, np.zeros((half_batch, 1)))
        d_loss = 0.5 * np.add(d_loss_real, d_loss_fake)


        # ---------------------
        #  Train Generator
        # ---------------------

        noise = np.random.normal(0, 1, (batch_size, 100))

        # The generator wants the discriminator to label the generated samples
        # as valid (ones)
        valid_y = np.array([1] * batch_size)

        # Train the generator
        g_loss = combined.train_on_batch(noise, valid_y)

        # Plot the progress
        print ("%d [D loss: %f, acc.: %.2f%%] [G loss: %f]" % (epoch, d_loss[0], 100*d_loss[1], g_loss))

        # If at save interval => save generated image samples
        if epoch % save_interval == 0:
            save_imgs(epoch)

In [9]:
img_rows = 6
img_cols = 360
channels = 1
img_shape = (img_rows, img_cols, channels)
optimizer = Adam(0.0002, 0.5)
optimizer_combined = Adam(0.0001, 0.5)

In [10]:
# Build and compile the discriminator
discriminator = build_discriminator()
discriminator.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
flatten_1 (Flatten)          (None, 2160)              0         
_________________________________________________________________
dense_1 (Dense)              (None, 512)               1106432   
_________________________________________________________________
leaky_re_lu_1 (LeakyReLU)    (None, 512)               0         
_________________________________________________________________
dense_2 (Dense)              (None, 256)               131328    
_________________________________________________________________
leaky_re_lu_2 (LeakyReLU)    (None, 256)               0         
_________________________________________________________________
dense_3 (Dense)              (None, 1)                 257       
Total params: 1,238,017
Trainable params: 1,238,017
Non-trainable params: 0
_________________________________________________________________


In [11]:
# Build and compile the generator
generator = build_generator()
generator.compile(loss='binary_crossentropy', optimizer=optimizer)

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_4 (Dense)              (None, 32)                3232      
_________________________________________________________________
leaky_re_lu_3 (LeakyReLU)    (None, 32)                0         
_________________________________________________________________
batch_normalization_1 (Batch (None, 32)                128       
_________________________________________________________________
dense_5 (Dense)              (None, 2160)              71280     
_________________________________________________________________
reshape_1 (Reshape)          (None, 6, 360, 1)         0         
Total params: 74,640
Trainable params: 74,576
Non-trainable params: 64
_________________________________________________________________


In [12]:
# The generator takes noise as input and generated imgs
z = Input(shape=(100,))
img = generator(z)

In [13]:
# For the combined model we will only train the generator
discriminator.trainable = False

# The valid takes generated images as input and determines validity
valid = discriminator(img)

# The combined model  (stacked generator and discriminator) takes
# noise as input => generates images => determines validity 
combined = Model(z, valid)
combined.compile(loss='binary_crossentropy', optimizer=optimizer)

In [14]:
train(epochs=2000, batch_size=64, save_interval=200)

0 [D loss: 0.683810, acc.: 37.50%] [G loss: 0.624079]


1 [D loss: 0.559395, acc.: 85.94%] [G loss: 0.624083]
2 [D loss: 0.440188, acc.: 95.31%] [G loss: 0.635589]
3 [D loss: 0.383659, acc.: 93.75%] [G loss: 0.644418]
4 [D loss: 0.339490, acc.: 90.62%] [G loss: 0.673686]
5 [D loss: 0.345841, acc.: 87.50%] [G loss: 0.720193]
6 [D loss: 0.348215, acc.: 87.50%] [G loss: 0.761666]
7 [D loss: 0.373879, acc.: 81.25%] [G loss: 0.805196]
8 [D loss: 0.306166, acc.: 82.81%] [G loss: 0.863466]
9 [D loss: 0.377845, acc.: 75.00%] [G loss: 0.895901]
10 [D loss: 0.354493, acc.: 85.94%] [G loss: 0.936397]
11 [D loss: 0.354962, acc.: 84.38%] [G loss: 1.008376]
12 [D loss: 0.269887, acc.: 93.75%] [G loss: 1.035024]
13 [D loss: 0.290927, acc.: 89.06%] [G loss: 1.086633]
14 [D loss: 0.279386, acc.: 90.62%] [G loss: 1.136752]
15 [D loss: 0.310261, acc.: 90.62%] [G loss: 1.189220]
16 [D loss: 0.290479, acc.: 89.06%] [G loss: 1.256200]
17 [D loss: 0.221321, acc.: 98.44%] [G loss: 1.321565]
18 [D loss: 0.216095, acc.: 96.88%] [G loss: 1.375322]
19 [D loss: 0.21324

150 [D loss: 0.117329, acc.: 95.31%] [G loss: 2.643030]
151 [D loss: 0.119831, acc.: 96.88%] [G loss: 2.642291]
152 [D loss: 0.152367, acc.: 92.19%] [G loss: 2.828656]
153 [D loss: 0.052221, acc.: 98.44%] [G loss: 2.756474]
154 [D loss: 0.130465, acc.: 95.31%] [G loss: 2.760949]
155 [D loss: 0.076543, acc.: 98.44%] [G loss: 2.828224]
156 [D loss: 0.155038, acc.: 92.19%] [G loss: 2.688816]
157 [D loss: 0.139169, acc.: 95.31%] [G loss: 2.629369]
158 [D loss: 0.156624, acc.: 93.75%] [G loss: 2.586581]
159 [D loss: 0.368484, acc.: 84.38%] [G loss: 2.303724]
160 [D loss: 0.234639, acc.: 89.06%] [G loss: 2.260779]
161 [D loss: 0.140550, acc.: 98.44%] [G loss: 2.481306]
162 [D loss: 0.120578, acc.: 96.88%] [G loss: 2.650541]
163 [D loss: 0.104101, acc.: 96.88%] [G loss: 2.651005]
164 [D loss: 0.165743, acc.: 90.62%] [G loss: 2.624848]
165 [D loss: 0.096809, acc.: 95.31%] [G loss: 2.617813]
166 [D loss: 0.104883, acc.: 96.88%] [G loss: 2.605442]
167 [D loss: 0.105035, acc.: 95.31%] [G loss: 2.

201 [D loss: 0.190984, acc.: 90.62%] [G loss: 2.444964]
202 [D loss: 0.216380, acc.: 87.50%] [G loss: 2.551170]
203 [D loss: 0.323689, acc.: 92.19%] [G loss: 2.461388]
204 [D loss: 0.163086, acc.: 93.75%] [G loss: 2.514653]
205 [D loss: 0.169584, acc.: 92.19%] [G loss: 2.612388]
206 [D loss: 0.191150, acc.: 89.06%] [G loss: 2.594213]
207 [D loss: 0.184567, acc.: 90.62%] [G loss: 2.696650]
208 [D loss: 0.156596, acc.: 93.75%] [G loss: 2.600200]
209 [D loss: 0.212339, acc.: 93.75%] [G loss: 2.661460]
210 [D loss: 0.147990, acc.: 93.75%] [G loss: 2.571961]
211 [D loss: 0.171613, acc.: 95.31%] [G loss: 2.616117]
212 [D loss: 0.122986, acc.: 98.44%] [G loss: 2.647120]
213 [D loss: 0.203114, acc.: 93.75%] [G loss: 2.716175]
214 [D loss: 0.257658, acc.: 89.06%] [G loss: 2.445478]
215 [D loss: 0.188394, acc.: 92.19%] [G loss: 2.548821]
216 [D loss: 0.217733, acc.: 89.06%] [G loss: 2.527555]
217 [D loss: 0.210856, acc.: 92.19%] [G loss: 2.576628]
218 [D loss: 0.245917, acc.: 87.50%] [G loss: 2.

349 [D loss: 0.114643, acc.: 96.88%] [G loss: 2.537306]
350 [D loss: 0.227387, acc.: 93.75%] [G loss: 2.539815]
351 [D loss: 0.194077, acc.: 93.75%] [G loss: 2.549695]
352 [D loss: 0.246636, acc.: 90.62%] [G loss: 2.677043]
353 [D loss: 0.208917, acc.: 92.19%] [G loss: 2.631412]
354 [D loss: 0.159673, acc.: 95.31%] [G loss: 2.573867]
355 [D loss: 0.126913, acc.: 96.88%] [G loss: 2.547177]
356 [D loss: 0.127460, acc.: 96.88%] [G loss: 2.528013]
357 [D loss: 0.198635, acc.: 93.75%] [G loss: 2.542697]
358 [D loss: 0.194564, acc.: 93.75%] [G loss: 2.504943]
359 [D loss: 0.218910, acc.: 90.62%] [G loss: 2.404725]
360 [D loss: 0.289145, acc.: 89.06%] [G loss: 2.426508]
361 [D loss: 0.108057, acc.: 96.88%] [G loss: 2.612874]
362 [D loss: 0.238127, acc.: 92.19%] [G loss: 2.625150]
363 [D loss: 0.141153, acc.: 95.31%] [G loss: 2.642863]
364 [D loss: 0.122339, acc.: 96.88%] [G loss: 2.594809]
365 [D loss: 0.180606, acc.: 93.75%] [G loss: 2.546185]
366 [D loss: 0.124824, acc.: 96.88%] [G loss: 2.

...

1546 [D loss: 0.228407, acc.: 92.19%] [G loss: 2.496583]
1547 [D loss: 0.144745, acc.: 95.31%] [G loss: 2.482685]
1548 [D loss: 0.155206, acc.: 95.31%] [G loss: 2.506399]
1549 [D loss: 0.121705, acc.: 96.88%] [G loss: 2.517715]
1550 [D loss: 0.082312, acc.: 98.44%] [G loss: 2.539569]
1551 [D loss: 0.048143, acc.: 100.00%] [G loss: 2.606399]
1552 [D loss: 0.127498, acc.: 96.88%] [G loss: 2.601785]
1553 [D loss: 0.045308, acc.: 100.00%] [G loss: 2.648624]
1554 [D loss: 0.082672, acc.: 98.44%] [G loss: 2.672908]
1555 [D loss: 0.200594, acc.: 92.19%] [G loss: 2.615148]
1556 [D loss: 0.305540, acc.: 89.06%] [G loss: 2.532675]
1557 [D loss: 0.165682, acc.: 95.31%] [G loss: 2.505182]
1558 [D loss: 0.258118, acc.: 90.62%] [G loss: 2.490362]
1559 [D loss: 0.203542, acc.: 93.75%] [G loss: 2.485817]
1560 [D loss: 0.121357, acc.: 96.88%] [G loss: 2.543138]
1561 [D loss: 0.086838, acc.: 98.44%] [G loss: 2.588499]
1562 [D loss: 0.082590, acc.: 98.44%] [G loss: 2.649878]
1563 [D loss: 0.138703, acc.:

1601 [D loss: 0.124097, acc.: 96.88%] [G loss: 2.659213]
1602 [D loss: 0.152775, acc.: 95.31%] [G loss: 2.674334]
1603 [D loss: 0.257485, acc.: 92.19%] [G loss: 2.629219]
1604 [D loss: 0.153487, acc.: 95.31%] [G loss: 2.706040]
1605 [D loss: 0.239700, acc.: 90.62%] [G loss: 2.663137]
1606 [D loss: 0.232465, acc.: 92.19%] [G loss: 2.612333]
1607 [D loss: 0.156835, acc.: 95.31%] [G loss: 2.618695]
1608 [D loss: 0.192511, acc.: 93.75%] [G loss: 2.616789]
1609 [D loss: 0.182639, acc.: 93.75%] [G loss: 2.660440]
1610 [D loss: 0.253701, acc.: 90.62%] [G loss: 2.595896]
1611 [D loss: 0.087954, acc.: 98.44%] [G loss: 2.637405]
1612 [D loss: 0.149179, acc.: 95.31%] [G loss: 2.633179]
1613 [D loss: 0.191319, acc.: 93.75%] [G loss: 2.619596]
1614 [D loss: 0.155410, acc.: 95.31%] [G loss: 2.620615]
1615 [D loss: 0.253988, acc.: 90.62%] [G loss: 2.623681]
1616 [D loss: 0.184612, acc.: 93.75%] [G loss: 2.595181]
1617 [D loss: 0.084145, acc.: 98.44%] [G loss: 2.639707]
1618 [D loss: 0.232504, acc.: 9

1751 [D loss: 0.116256, acc.: 96.88%] [G loss: 2.666300]
1752 [D loss: 0.155654, acc.: 95.31%] [G loss: 2.700342]
1753 [D loss: 0.064553, acc.: 98.44%] [G loss: 2.707007]
1754 [D loss: 0.187973, acc.: 93.75%] [G loss: 2.660316]
1755 [D loss: 0.078608, acc.: 98.44%] [G loss: 2.715883]
1756 [D loss: 0.076200, acc.: 98.44%] [G loss: 2.731272]
1757 [D loss: 0.164689, acc.: 95.31%] [G loss: 2.748313]
1758 [D loss: 0.083727, acc.: 98.44%] [G loss: 2.785051]
1759 [D loss: 0.113039, acc.: 96.88%] [G loss: 2.807973]
1760 [D loss: 0.251893, acc.: 92.19%] [G loss: 2.738696]
1761 [D loss: 0.196475, acc.: 93.75%] [G loss: 2.701404]
1762 [D loss: 0.074631, acc.: 98.44%] [G loss: 2.749270]
1763 [D loss: 0.200573, acc.: 93.75%] [G loss: 2.734675]
1764 [D loss: 0.077553, acc.: 98.44%] [G loss: 2.784853]
1765 [D loss: 0.194978, acc.: 93.75%] [G loss: 2.767571]
1766 [D loss: 0.120550, acc.: 96.88%] [G loss: 2.769490]
1767 [D loss: 0.271979, acc.: 90.62%] [G loss: 2.687598]
1768 [D loss: 0.080972, acc.: 9

1801 [D loss: 0.249823, acc.: 92.19%] [G loss: 2.520222]
1802 [D loss: 0.272224, acc.: 90.62%] [G loss: 2.483541]
1803 [D loss: 0.194287, acc.: 93.75%] [G loss: 2.471776]
1804 [D loss: 0.122290, acc.: 96.88%] [G loss: 2.500095]
1805 [D loss: 0.231438, acc.: 92.19%] [G loss: 2.528044]
1806 [D loss: 0.090064, acc.: 98.44%] [G loss: 2.583571]
1807 [D loss: 0.165046, acc.: 95.31%] [G loss: 2.530928]
1808 [D loss: 0.052728, acc.: 100.00%] [G loss: 2.583229]
1809 [D loss: 0.157941, acc.: 95.31%] [G loss: 2.604008]
1810 [D loss: 0.151194, acc.: 95.31%] [G loss: 2.636507]
1811 [D loss: 0.083258, acc.: 98.44%] [G loss: 2.655761]
1812 [D loss: 0.118133, acc.: 96.88%] [G loss: 2.697890]
1813 [D loss: 0.157063, acc.: 95.31%] [G loss: 2.660979]
1814 [D loss: 0.225752, acc.: 92.19%] [G loss: 2.625290]
1815 [D loss: 0.116439, acc.: 96.88%] [G loss: 2.631861]
1816 [D loss: 0.309535, acc.: 89.06%] [G loss: 2.596732]
1817 [D loss: 0.118938, acc.: 96.88%] [G loss: 2.662161]
1818 [D loss: 0.114196, acc.: 

1951 [D loss: 0.115406, acc.: 96.88%] [G loss: 2.755116]
1952 [D loss: 0.124128, acc.: 96.88%] [G loss: 2.736521]
1953 [D loss: 0.083697, acc.: 98.44%] [G loss: 2.800792]
1954 [D loss: 0.080385, acc.: 98.44%] [G loss: 2.782240]
1955 [D loss: 0.077903, acc.: 98.44%] [G loss: 2.807444]
1956 [D loss: 0.114643, acc.: 96.88%] [G loss: 2.796587]
1957 [D loss: 0.097241, acc.: 98.44%] [G loss: 2.789675]
1958 [D loss: 0.159371, acc.: 95.31%] [G loss: 2.763048]
1959 [D loss: 0.214747, acc.: 93.75%] [G loss: 2.699660]
1960 [D loss: 0.271677, acc.: 92.19%] [G loss: 2.653405]
1961 [D loss: 0.117606, acc.: 96.88%] [G loss: 2.665311]
1962 [D loss: 0.230014, acc.: 92.19%] [G loss: 2.619421]
1963 [D loss: 0.233163, acc.: 92.19%] [G loss: 2.625873]
1964 [D loss: 0.125952, acc.: 96.88%] [G loss: 2.696040]
1965 [D loss: 0.118226, acc.: 96.88%] [G loss: 2.723883]
1966 [D loss: 0.196485, acc.: 93.75%] [G loss: 2.715796]
1967 [D loss: 0.157309, acc.: 95.31%] [G loss: 2.757981]
1968 [D loss: 0.148081, acc.: 9